In [57]:
import pandas as pd
from config import config
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import os

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
    
plt.rcParams['figure.figsize'] = [7, 7]

In [58]:
# create cache directory
os.makedirs('cache', exist_ok=True)

assuming you have data and its placed where is should ("python3 fetch_data.py")

Business Understanding

* Is the salary correlated with some programming language, framework or platform?
* How much influence have the country the developer is working ?
* Are we able to predict salary based on the stack overflow data?

In [59]:
config[-1]

{'year': '2020',
 'url': 'https://drive.google.com/uc?id=1dfGerWeWkcyQ9GX9x20rdSGj7WtEpzBB&export=download',
 'local_path': 'data/2020.zip',
 'unpack_path': 'data/unpack/2020.zip',
 'data_path': 'data/unpack/2020.zip/survey_results_public.csv',
 'json_path': '2020.json',
 'numeric_columns': ['ConvertedComp',
  'Age',
  'Age1stCode',
  'YearsCode',
  'YearsCodePro',
  'WorkWeekHrs'],
 'leave_columns': ['CompTotal', 'Respondent']}

In [60]:
df_raw = pd.read_csv(config[-1]['data_path'], dtype=str)

salary encoded here as `ConvertedComp` - its in USD

In [61]:
len(df_raw)

64461

In [62]:
df_raw.columns

Index(['Respondent', 'MainBranch', 'Hobbyist', 'Age', 'Age1stCode', 'CompFreq',
       'CompTotal', 'ConvertedComp', 'Country', 'CurrencyDesc',
       'CurrencySymbol', 'DatabaseDesireNextYear', 'DatabaseWorkedWith',
       'DevType', 'EdLevel', 'Employment', 'Ethnicity', 'Gender', 'JobFactors',
       'JobSat', 'JobSeek', 'LanguageDesireNextYear', 'LanguageWorkedWith',
       'MiscTechDesireNextYear', 'MiscTechWorkedWith',
       'NEWCollabToolsDesireNextYear', 'NEWCollabToolsWorkedWith', 'NEWDevOps',
       'NEWDevOpsImpt', 'NEWEdImpt', 'NEWJobHunt', 'NEWJobHuntResearch',
       'NEWLearn', 'NEWOffTopic', 'NEWOnboardGood', 'NEWOtherComms',
       'NEWOvertime', 'NEWPurchaseResearch', 'NEWPurpleLink', 'NEWSOSites',
       'NEWStuck', 'OpSys', 'OrgSize', 'PlatformDesireNextYear',
       'PlatformWorkedWith', 'PurchaseWhat', 'Sexuality', 'SOAccount',
       'SOComm', 'SOPartFreq', 'SOVisitFreq', 'SurveyEase', 'SurveyLength',
       'Trans', 'UndergradMajor', 'WebframeDesireNextYear',
  

The data of stackoverflow contains a lot of columns (61 in total). Most of the data is a string of a set of possible answers. Only a small amount contains floating point values. In total, we have 64461 answers, where about 53.9% (34756) contain an answer related to their current job salary, less than we got compared to the job satisfaction we analysed at the beginning of this year (70%).

In [63]:
df = df_raw[~ df_raw['ConvertedComp'].isnull()]

In [64]:
float(len(df)) / len(df_raw)

0.5391787282232667

In [65]:
# del df_raw

In [66]:
len(df)

34756

In [67]:
df['CompTotal'].describe()

count     34756
unique     2997
top       1e+05
freq        767
Name: CompTotal, dtype: object

In [68]:
set(df['CompFreq'])

{'Monthly', 'Weekly', 'Yearly'}

We have a total 2997 unique values. But this values can be references as 'Monthly', 'Weekly' and 'Yearly' - that needs to be considered then doing the data preparation.

# Section 3: Data Preparation

## Selection

All rows that don't have a salary defined, will where removed from the dataset.

# Construct

I created new columns out of the existings ones in order to extract the features we want to analyse. This was done for all columns, resulting in a very wide table. Run `preprocessing.py` in the project directory.

In [69]:
df_raw.columns

Index(['Respondent', 'MainBranch', 'Hobbyist', 'Age', 'Age1stCode', 'CompFreq',
       'CompTotal', 'ConvertedComp', 'Country', 'CurrencyDesc',
       'CurrencySymbol', 'DatabaseDesireNextYear', 'DatabaseWorkedWith',
       'DevType', 'EdLevel', 'Employment', 'Ethnicity', 'Gender', 'JobFactors',
       'JobSat', 'JobSeek', 'LanguageDesireNextYear', 'LanguageWorkedWith',
       'MiscTechDesireNextYear', 'MiscTechWorkedWith',
       'NEWCollabToolsDesireNextYear', 'NEWCollabToolsWorkedWith', 'NEWDevOps',
       'NEWDevOpsImpt', 'NEWEdImpt', 'NEWJobHunt', 'NEWJobHuntResearch',
       'NEWLearn', 'NEWOffTopic', 'NEWOnboardGood', 'NEWOtherComms',
       'NEWOvertime', 'NEWPurchaseResearch', 'NEWPurpleLink', 'NEWSOSites',
       'NEWStuck', 'OpSys', 'OrgSize', 'PlatformDesireNextYear',
       'PlatformWorkedWith', 'PurchaseWhat', 'Sexuality', 'SOAccount',
       'SOComm', 'SOPartFreq', 'SOVisitFreq', 'SurveyEase', 'SurveyLength',
       'Trans', 'UndergradMajor', 'WebframeDesireNextYear',
  

In [70]:


def load(column:str,  year:int) -> pd.DataFrame:
    '''
    Calculate features and cache result. Further calls will return the precalculated results
    
    :param df: (pd.DataFrame) The DataFrame with the data to be processed
    :param column: (str) The column with the data to process
    :param year: (int) the year of the data, used as cache key
    :returns: go.Figure, ready to use plotly figure
    '''
    
    cache_key = f"{year}_{column}.json"
    cache_path = os.path.join('cache', cache_key)
    if os.path.exists(cache_path):
        return pd.read_json(cache_path, lines=True)

def plot_distribution(column:str, year:int, sort_by:str='values') -> go.Figure:
    '''
    Plots the sum of the positives of a partical column with multilable values.
    
    :param df: (pd.DataFrame) The DataFrame with the data to be plotted
    :param column: (str) The column with the data to plot
    :returns: go.Figure, ready to use plotly figure
    '''
    
    df_cached = load(column, year)
    if "CompTotal" in df_cached.columns:
        df_cached = df_cached.drop("CompTotal", axis=1)
    
    if "Respondent" in df_cached.columns:
        df_cached = df_cached.drop("Respondent", axis=1)
   
    if sort_by == 'values':
        df_sum = df_cached.sum().to_frame()
        df_sorted = df_sum.sort_values(by=0, ascending=True)
        y = list(map(lambda x: x.split('_')[-1], df_sorted.index))
        x = df_sorted.values.flatten()
        fig = go.Figure(data=[go.Bar(x=x, y=y, text=y, orientation='h')])
    elif sort_by == 'numeric': 
        col = df_cached.columns
        real_col = list(filter(lambda x: 'NA' not in x, col))[0]
        na_col = list(filter(lambda x: 'NA' in x, col))[0]
        x = df_cached[df_cached[na_col].isnull()][real_col]
        fig = go.Figure(data=[go.Histogram(x=x, bingroup=25)])
    return fig


# Constructed data (and their analysis)

## Numeric Values
When we have a column with a numeric value, we can directly use it as a feature. No scaling is done as I assume that the NN is able to handle the unscaled data correctly. If a value is nan, we extract it in a new column naming it `<column_name>_NA`. This prevents the deletion of the entire row only because (some) information is missing. Nan column are not shown here.

### Hours of work by week
This column reflect the number of hours worked.

In [71]:
plot_distribution('WorkWeekHrs', 2020, 'numeric').show()

By far the most work at 40 h a week. Considering 7 * 24 = 168 h as max, and 5h sleepping (what is not enough for myself)  7 * 5 = 35h , resulting in all values more than 120h as really unrealistic.  

### Age
This column reflect the number of age of the user.

In [72]:
plot_distribution('Age', 2020, 'numeric').show()

Most participants are about 25 year old. We have a heavy outlier with 280 years than can be consiered wrong data, and lot of wrong locking values ( I would assume everything more than 70 looks really unrealistic as target group for stack overflow)

### Age 1st Code
This column reflect the Age that the user was, as they started to code.

In [73]:
plot_distribution('Age1stCode', 2020, 'numeric').show()

Column as not sorted here as "Younger than 5y" and "Older than 85" is not a number, and this converts the entire `DataFrame` into strings. Most start between 12 and 18, what seems realistic.

### YearsCode
This column reflect the number of Years that the user code.

In [74]:
plot_distribution('YearsCode', 2020, 'numeric').show()

Most users have 10 years of coding experience in general.

### YearsCodePro
This column reflect the number of years of coding in a professional environment.

In [75]:
plot_distribution('YearsCodePro', 2020, 'numeric').show()

Most of the users have a quite low amount of coding experience in a professional environment. This can be an indicator that they are more likley to use stack overflow than a more experience developer - they can read up directly the documentation of the particular framework. 

## Categorical Features
This will give a inside on the categorical data we found. Some answers are exclusive, for example only one company size could be seleted. But for some other answers, entire sets could be selected, like in the used programming languages. Both sources where one-hot encoded.

### CompFreq
This column reflect the payment frequency. 

In [76]:
plot_distribution('CompFreq', 2020, 'values').show()

19107 yearly salary information, 14680 Monthly and 969 Weekly. Most don't respond to the answer.

In [77]:
plot_distribution('Country', 2020).show()

We have a lot on countries with a low amount of responses. Its possible that they get removed when we split on train and test set. 12k answers from the USA than with fast dropping distributions.

In [78]:
plot_distribution('DatabaseDesireNextYear', 2020).show()

In [79]:
plot_distribution('OrgSize', 2020).show()

# Label
As we want to predict the salary, we use the `ConvertedComp` column in the data. The payment frequency and the different currencies have been converted to one base and allow a better comparision. From the stack overflow schema file:

```
ConvertedComp,"Salary converted to annual USD salaries using the exchange rate on 2020-02-19, assuming 12 | working months and 50 working weeks."
```

In [80]:
plot_distribution('ConvertedComp', 2020, 'numeric').show()

Most have a low annual income with 10k. But this may be a lot amount of money, depending on the geographical position of the user. After 200k the amount of items in the bucket gets low - only a few users have such high amount of income.

# Modelling
As I can't fit the entire dataset into memory, I build up a scala application to run it on real spark cluster.